In [1]:
import torch
import time
import numpy as np
import matplotlib.pyplot as plt
from sklearn.metrics import precision_score, f1_score
# from nltk.translate.bleu_score import corpus_bleu, SmoothingFunction
from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction
from transformer import Transformer # this is from the transformer.py file

In [2]:
START_TOKEN = '<START>'
PADDING_TOKEN = '<PADDING>'
END_TOKEN = '<END>'

kannada_vocabulary = [START_TOKEN, ' ', '!', '"', '#', '$', '%', '&', "'", '(', ')', '*', '+', ',', '-', '.', '/', 
                      '0', '1', '2', '3', '4', '5', '6', '7', '8', '9', ':', '<', '=', '>', '?', 'ˌ', 
                      'ँ', 'ఆ', 'ఇ', 'ా', 'ి', 'ీ', 'ు', 'ూ', 
                      'ಅ', 'ಆ', 'ಇ', 'ಈ', 'ಉ', 'ಊ', 'ಋ', 'ೠ', 'ಌ', 'ಎ', 'ಏ', 'ಐ', 'ಒ', 'ಓ', 'ಔ', 
                      'ಕ', 'ಖ', 'ಗ', 'ಘ', 'ಙ', 
                      'ಚ', 'ಛ', 'ಜ', 'ಝ', 'ಞ', 
                      'ಟ', 'ಠ', 'ಡ', 'ಢ', 'ಣ', 
                      'ತ', 'ಥ', 'ದ', 'ಧ', 'ನ', 
                      'ಪ', 'ಫ', 'ಬ', 'ಭ', 'ಮ', 
                      'ಯ', 'ರ', 'ಱ', 'ಲ', 'ಳ', 'ವ', 'ಶ', 'ಷ', 'ಸ', 'ಹ', 
                      '಼', 'ಽ', 'ಾ', 'ಿ', 'ೀ', 'ು', 'ೂ', 'ೃ', 'ೄ', 'ೆ', 'ೇ', 'ೈ', 'ೊ', 'ೋ', 'ೌ', '್', 'ೕ', 'ೖ', 'ೞ', 'ೣ', 'ಂ', 'ಃ', 
                      '೦', '೧', '೨', '೩', '೪', '೫', '೬', '೭', '೮', '೯', PADDING_TOKEN, END_TOKEN]

english_vocabulary = [START_TOKEN, ' ', '!', '"', '#', '$', '%', '&', "'", '(', ')', '*', '+', ',', '-', '.', '/', 
                        '0', '1', '2', '3', '4', '5', '6', '7', '8', '9',
                        ':', '<', '=', '>', '?', '@',
                        '[', '\\', ']', '^', '_', '`', 
                        'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l',
                        'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 
                        'y', 'z', 
                        '{', '|', '}', '~', PADDING_TOKEN, END_TOKEN]

In [3]:
print(kannada_vocabulary)
print(english_vocabulary)

['<START>', ' ', '!', '"', '#', '$', '%', '&', "'", '(', ')', '*', '+', ',', '-', '.', '/', '0', '1', '2', '3', '4', '5', '6', '7', '8', '9', ':', '<', '=', '>', '?', 'ˌ', 'ँ', 'ఆ', 'ఇ', 'ా', 'ి', 'ీ', 'ు', 'ూ', 'ಅ', 'ಆ', 'ಇ', 'ಈ', 'ಉ', 'ಊ', 'ಋ', 'ೠ', 'ಌ', 'ಎ', 'ಏ', 'ಐ', 'ಒ', 'ಓ', 'ಔ', 'ಕ', 'ಖ', 'ಗ', 'ಘ', 'ಙ', 'ಚ', 'ಛ', 'ಜ', 'ಝ', 'ಞ', 'ಟ', 'ಠ', 'ಡ', 'ಢ', 'ಣ', 'ತ', 'ಥ', 'ದ', 'ಧ', 'ನ', 'ಪ', 'ಫ', 'ಬ', 'ಭ', 'ಮ', 'ಯ', 'ರ', 'ಱ', 'ಲ', 'ಳ', 'ವ', 'ಶ', 'ಷ', 'ಸ', 'ಹ', '಼', 'ಽ', 'ಾ', 'ಿ', 'ೀ', 'ು', 'ೂ', 'ೃ', 'ೄ', 'ೆ', 'ೇ', 'ೈ', 'ೊ', 'ೋ', 'ೌ', '್', 'ೕ', 'ೖ', 'ೞ', 'ೣ', 'ಂ', 'ಃ', '೦', '೧', '೨', '೩', '೪', '೫', '೬', '೭', '೮', '೯', '<PADDING>', '<END>']
['<START>', ' ', '!', '"', '#', '$', '%', '&', "'", '(', ')', '*', '+', ',', '-', '.', '/', '0', '1', '2', '3', '4', '5', '6', '7', '8', '9', ':', '<', '=', '>', '?', '@', '[', '\\', ']', '^', '_', '`', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', '{', '|', '}', '~', '<P

In [4]:
index_to_kannada = {k:v for k,v in enumerate(kannada_vocabulary)}
kannada_to_index = {v:k for k,v in enumerate(kannada_vocabulary)}
index_to_english = {k:v for k,v in enumerate(english_vocabulary)}
english_to_index = {v:k for k,v in enumerate(english_vocabulary)}

In [5]:
print("Index : Kannada")
print(index_to_kannada)
print("\nKannada : Index")
print(kannada_to_index)
print("\n\nIndex : English")
print(index_to_english)
print("\nEnglish : Index")
print(english_to_index)

Index : Kannada
{0: '<START>', 1: ' ', 2: '!', 3: '"', 4: '#', 5: '$', 6: '%', 7: '&', 8: "'", 9: '(', 10: ')', 11: '*', 12: '+', 13: ',', 14: '-', 15: '.', 16: '/', 17: '0', 18: '1', 19: '2', 20: '3', 21: '4', 22: '5', 23: '6', 24: '7', 25: '8', 26: '9', 27: ':', 28: '<', 29: '=', 30: '>', 31: '?', 32: 'ˌ', 33: 'ँ', 34: 'ఆ', 35: 'ఇ', 36: 'ా', 37: 'ి', 38: 'ీ', 39: 'ు', 40: 'ూ', 41: 'ಅ', 42: 'ಆ', 43: 'ಇ', 44: 'ಈ', 45: 'ಉ', 46: 'ಊ', 47: 'ಋ', 48: 'ೠ', 49: 'ಌ', 50: 'ಎ', 51: 'ಏ', 52: 'ಐ', 53: 'ಒ', 54: 'ಓ', 55: 'ಔ', 56: 'ಕ', 57: 'ಖ', 58: 'ಗ', 59: 'ಘ', 60: 'ಙ', 61: 'ಚ', 62: 'ಛ', 63: 'ಜ', 64: 'ಝ', 65: 'ಞ', 66: 'ಟ', 67: 'ಠ', 68: 'ಡ', 69: 'ಢ', 70: 'ಣ', 71: 'ತ', 72: 'ಥ', 73: 'ದ', 74: 'ಧ', 75: 'ನ', 76: 'ಪ', 77: 'ಫ', 78: 'ಬ', 79: 'ಭ', 80: 'ಮ', 81: 'ಯ', 82: 'ರ', 83: 'ಱ', 84: 'ಲ', 85: 'ಳ', 86: 'ವ', 87: 'ಶ', 88: 'ಷ', 89: 'ಸ', 90: 'ಹ', 91: '಼', 92: 'ಽ', 93: 'ಾ', 94: 'ಿ', 95: 'ೀ', 96: 'ು', 97: 'ೂ', 98: 'ೃ', 99: 'ೄ', 100: 'ೆ', 101: 'ೇ', 102: 'ೈ', 103: 'ೊ', 104: 'ೋ', 105: 'ೌ', 106: '್', 107: 'ೕ', 108: 'ೖ

In [6]:
with open('../datasets/En-Kn/train.en', 'r') as file:
    english_sentences = file.readlines()
with open('../datasets/En-Kn/train.kn', 'r') as file:
    kannada_sentences = file.readlines()

In [7]:
len(english_sentences), len( kannada_sentences)

(4093524, 4093524)

In [8]:
TOTAL_SENTENCES = 1000000
english_sentences = english_sentences[:TOTAL_SENTENCES]
kannada_sentences = kannada_sentences[:TOTAL_SENTENCES]
english_sentences = [sentence.rstrip('\n').lower() for sentence in english_sentences]
kannada_sentences = [sentence.rstrip('\n') for sentence in kannada_sentences]

In [9]:
len(english_sentences), len( kannada_sentences)

(1000000, 1000000)

In [10]:
english_sentences[:10]

['hes a scientist.',
 "'but we speak the truth aur ye sach hai ke gujarat mein vikas pagal hogaya hai,'' rahul gandhi further said in banaskantha",
 '8 lakh crore have been looted.',
 'i read a lot into this as well.',
 "she was found dead with the phone's battery exploded close to her head the following morning.",
 'how did mankind come under satans rival sovereignty?',
 'and then i became prime minister.',
 'what about corruption?',
 'no differences',
 '"""the shooting of the film is 90 percent done."']

In [11]:
kannada_sentences[:10]

['ಇವರು ಸಂಶೋಧಕ ಸ್ವಭಾವದವರು.',
 '"ಆದರೆ ಸತ್ಯ ಹೊರ ಬಂದೇ ಬರುತ್ತದೆ ಎಂದು ಹೇಳಿದ ರಾಹುಲ್ ಗಾಂಧಿ, ""ಸೂರತ್ ಜನರು ಚೀನಾದ ಜತೆ ಸ್ಪರ್ಧೆ ನಡೆಸುತ್ತಿದ್ದಾರೆ"',
 'ಕಳ್ಳತನವಾಗಿದ್ದ 8 ಲಕ್ಷ ರೂ.',
 'ಇದರ ಬಗ್ಗೆ ನಾನೂ ಸಾಕಷ್ಟು ಓದಿದ್ದೇನೆ.',
 'ಆಕೆಯ ತಲೆಯ ಹತ್ತಿರ ಇರಿಸಿಕೊಂಡಿದ್ದ ಫೋನ್\u200cನ ಬ್ಯಾಟರಿ ಸ್ಫೋಟಗೊಂಡು ಆಕೆ ಮೃತಪಟ್ಟಿದ್ದಾಳೆ ಎನ್ನಲಾಗಿದೆ.',
 'ಮಾನವಕುಲವು ಸೈತಾನನ ಆಳಿಕೆಯ ಕೆಳಗೆ ಬಂದದ್ದು ಹೇಗೆ?',
 'ನಂತರ ಪ್ರಧಾನಿ ಕೂಡ ಆಗುತ್ತೇನೆ.',
 'ಭ್ರಷ್ಟಾಚಾರ ಏಕಿದೆ?',
 '‘ಅನುಪಾತದಲ್ಲಿ ವ್ಯತ್ಯಾಸವಿಲ್ಲ’',
 'ಆ ಚಿತ್ರದ ಶೇ 90ರಷ್ಟು ಚಿತ್ರೀಕರಣವೂ ಈಗಾಗಲೇ ಮುಗಿದು ಹೋಗಿದೆ.']

In [12]:
max(len(x) for x in kannada_sentences), max(len(x) for x in english_sentences)

(10522, 4677)

In [13]:
import numpy as np
PERCENTILE = 97
print( f"{PERCENTILE}th percentile length Kannada: {np.percentile([len(x) for x in kannada_sentences], PERCENTILE)}" )
print( f"{PERCENTILE}th percentile length English: {np.percentile([len(x) for x in english_sentences], PERCENTILE)}" )

97th percentile length Kannada: 172.0
97th percentile length English: 177.0


In [14]:
max_sequence_length = 200

def is_Valid_Tokens(sentence, vocab):
    for token in list(set(sentence)):
        if token not in vocab:
            return False
    return True

def is_Valide_Length(sentence, max_sequence_length):
    return len(list(sentence)) < (max_sequence_length-1) #need to re-add the <END> token so leaving space for it

valid_sentence_indicies = []

for index in range(len(kannada_sentences)):
    kannada_sentence, english_sentence = kannada_sentences[index], english_sentences[index]
    if is_Valide_Length(kannada_sentence, max_sequence_length) and is_Valide_Length(english_sentence, max_sequence_length) and is_Valid_Tokens(kannada_sentence, kannada_vocabulary):
        valid_sentence_indicies.append(index)
        
# print(valid_sentence_indicies)
print(f"Number of senteces: {len(kannada_sentences)}")
print(f"Number of valid sentences: {len(valid_sentence_indicies)}")

Number of senteces: 1000000
Number of valid sentences: 818801


In [15]:
kannada_sentences = [kannada_sentences[i] for i in valid_sentence_indicies]
english_sentences = [english_sentences[i] for i in valid_sentence_indicies]

In [16]:
kannada_sentences[:5], english_sentences[:5]

(['ಇವರು ಸಂಶೋಧಕ ಸ್ವಭಾವದವರು.',
  '"ಆದರೆ ಸತ್ಯ ಹೊರ ಬಂದೇ ಬರುತ್ತದೆ ಎಂದು ಹೇಳಿದ ರಾಹುಲ್ ಗಾಂಧಿ, ""ಸೂರತ್ ಜನರು ಚೀನಾದ ಜತೆ ಸ್ಪರ್ಧೆ ನಡೆಸುತ್ತಿದ್ದಾರೆ"',
  'ಕಳ್ಳತನವಾಗಿದ್ದ 8 ಲಕ್ಷ ರೂ.',
  'ಇದರ ಬಗ್ಗೆ ನಾನೂ ಸಾಕಷ್ಟು ಓದಿದ್ದೇನೆ.',
  'ಮಾನವಕುಲವು ಸೈತಾನನ ಆಳಿಕೆಯ ಕೆಳಗೆ ಬಂದದ್ದು ಹೇಗೆ?'],
 ['hes a scientist.',
  "'but we speak the truth aur ye sach hai ke gujarat mein vikas pagal hogaya hai,'' rahul gandhi further said in banaskantha",
  '8 lakh crore have been looted.',
  'i read a lot into this as well.',
  'how did mankind come under satans rival sovereignty?'])

In [17]:
import torch

d_model = 512
batch_size = 30
ffn_hidden = 2048
num_heads = 8
drop_prob = 0.1
num_layers = 1
max_sequence_length = 200
kn_vocab_size = len(kannada_vocabulary)

transformer = Transformer(d_model, 
                          ffn_hidden,
                          num_heads, 
                          drop_prob, 
                          num_layers, 
                          max_sequence_length,
                          kn_vocab_size,
                          english_to_index,
                          kannada_to_index,
                          START_TOKEN, 
                          END_TOKEN, 
                          PADDING_TOKEN)

In [18]:
from torch.utils.data import Dataset, DataLoader

class TextDataset(Dataset):

    def __init__(self, english_sentences, kannada_sentences):
        self.english_sentences = english_sentences
        self.kannada_sentences = kannada_sentences

    def __len__(self):
        return len(self.english_sentences)

    def __getitem__(self, idx):
        return self.english_sentences[idx], self.kannada_sentences[idx]

In [19]:
dataset = TextDataset(english_sentences, kannada_sentences)

In [20]:
len(dataset)

818801

In [21]:
dataset[:1]

(['hes a scientist.'], ['ಇವರು ಸಂಶೋಧಕ ಸ್ವಭಾವದವರು.'])

In [22]:
train_loader = DataLoader(dataset, batch_size)
iterator = iter(train_loader)

In [23]:
for batch_num, batch in enumerate(iterator):
    print(batch)
    if batch_num > 3:
        break

[('hes a scientist.', "'but we speak the truth aur ye sach hai ke gujarat mein vikas pagal hogaya hai,'' rahul gandhi further said in banaskantha", '8 lakh crore have been looted.', 'i read a lot into this as well.', 'how did mankind come under satans rival sovereignty?', 'and then i became prime minister.', 'what about corruption?', '"""the shooting of the film is 90 percent done."', 'the special statute', '"then the king said to ittai the gittite, ""why do you also go with us? return, and stay with the king. for you are a foreigner, and also an exile. return to your own place."', 'what happened at the un general assembly?', 'the meeting was attended by prime minister narendra modi, home minister amit shah and defence minister rajnath singh, among others.', 'it has been under discussion for a long time.', 'buses cannot get there.', 'why then this tradition was not thought of?', 'kashmiri youth join indian army', 'basic amenities elude this village', 'off-budget borrowings of the state

In [24]:
from torch import nn

criterian = nn.CrossEntropyLoss(ignore_index=kannada_to_index[PADDING_TOKEN],
                                reduction='none')

# When computing the loss, we are ignoring cases when the label is the padding token
for params in transformer.parameters():
    if params.dim() > 1:
        nn.init.xavier_uniform_(params)

optim = torch.optim.Adam(transformer.parameters(), lr=1e-4)
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
# device = torch.device('cpu')
print(device)

cuda


In [25]:
NEG_INFTY = -1e9

def create_masks(eng_batch, kn_batch):
    num_sentences = len(eng_batch)
    look_ahead_mask = torch.full([max_sequence_length, max_sequence_length] , True)
    look_ahead_mask = torch.triu(look_ahead_mask, diagonal=1)
    encoder_padding_mask = torch.full([num_sentences, max_sequence_length, max_sequence_length] , False)
    decoder_padding_mask_self_attention = torch.full([num_sentences, max_sequence_length, max_sequence_length] , False)
    decoder_padding_mask_cross_attention = torch.full([num_sentences, max_sequence_length, max_sequence_length] , False)

    for idx in range(num_sentences):
        eng_sentence_length, kn_sentence_length = len(eng_batch[idx]), len(kn_batch[idx])
        eng_chars_to_padding_mask = np.arange(eng_sentence_length + 1, max_sequence_length)
        kn_chars_to_padding_mask = np.arange(kn_sentence_length + 1, max_sequence_length)
        encoder_padding_mask[idx, :, eng_chars_to_padding_mask] = True
        encoder_padding_mask[idx, eng_chars_to_padding_mask, :] = True
        decoder_padding_mask_self_attention[idx, :, kn_chars_to_padding_mask] = True
        decoder_padding_mask_self_attention[idx, kn_chars_to_padding_mask, :] = True
        decoder_padding_mask_cross_attention[idx, :, eng_chars_to_padding_mask] = True
        decoder_padding_mask_cross_attention[idx, kn_chars_to_padding_mask, :] = True

    encoder_self_attention_mask = torch.where(encoder_padding_mask, NEG_INFTY, 0)
    decoder_self_attention_mask =  torch.where(look_ahead_mask + decoder_padding_mask_self_attention, NEG_INFTY, 0)
    decoder_cross_attention_mask = torch.where(decoder_padding_mask_cross_attention, NEG_INFTY, 0)
    return encoder_self_attention_mask, decoder_self_attention_mask, decoder_cross_attention_mask

In [ ]:
#Training with Accuracy for each epoch and final trained transformer

transformer.train()
transformer.to(device)
total_loss = 0
num_epochs = 50
accuracy_list = []
f_score_list = []
loss_list = []
precision_list = []
kannada_translation_list = []
kannada_prediction_list = []
english_list = []
bleu_score_list = []


for epoch in range(num_epochs):
    print(f"Epoch {epoch}")
    iterator = iter(train_loader)
    total_correct_predictions = 0
    total_predictions = 0
    total_loss = 0

    for batch_num, batch in enumerate(iterator):
        transformer.train()
        eng_batch, kn_batch = batch
        encoder_self_attention_mask, decoder_self_attention_mask, decoder_cross_attention_mask = create_masks(eng_batch, kn_batch)
        optim.zero_grad()
        kn_predictions = transformer(eng_batch,
                                    kn_batch,
                                    encoder_self_attention_mask.to(device), 
                                    decoder_self_attention_mask.to(device), 
                                    decoder_cross_attention_mask.to(device),
                                    enc_start_token=False,
                                    enc_end_token=False,
                                    dec_start_token=True,
                                    dec_end_token=True)
        labels = transformer.decoder.sentence_embedding.batch_tokenize(kn_batch, start_token=False, end_token=True)
        loss = criterian(
            kn_predictions.view(-1, kn_vocab_size).to(device),
            labels.view(-1).to(device)
        ).to(device)
        valid_indices = torch.where(labels.view(-1) == kannada_to_index[PADDING_TOKEN], False, True)
        loss = loss.sum() / valid_indices.sum()
        loss.backward()
        optim.step()
        total_loss += loss.item()

        # Compute accuracy
        predictions = torch.argmax(kn_predictions, dim=2)
        num_correct = torch.sum(predictions == labels).item()
        total_correct_predictions += num_correct
        total_predictions += predictions.numel()
        
        if batch_num % 100 == 0:
            print(f"Iteration {batch_num} : {loss.item()}")
            print(f"English: {eng_batch[0]}")
            print(f"Kannada Translation: {kn_batch[0]}")
            kn_sentence_predicted = torch.argmax(kn_predictions[0], axis=1)
            predicted_sentence = ""
            for idx in kn_sentence_predicted:
                if idx == kannada_to_index[END_TOKEN]:
                    break
                predicted_sentence += index_to_kannada[idx.item()]
            print(f"Kannada Prediction: {predicted_sentence}")
            
            # Store Kannada translations and predictions
            english_list.append(eng_batch[0])
            kannada_translation_list.append(kn_batch[0])
            kannada_prediction_list.append(predicted_sentence)
            
            reference = [kn_batch[0].split()]  # Actual translation (reference)
            hypothesis = predicted_sentence.split()  # Predicted translation (hypothesis)
            
            # Calculate BLEU score
            smooth = SmoothingFunction()
            bleu_score = sentence_bleu(reference, hypothesis, smoothing_function=smooth.method1)
            print(f"Bleu Score: {bleu_score}")
            bleu_score_list.append(bleu_score)
            
            transformer.eval()
            kn_sentence = ("",)
            eng_sentence = ("should we go to the mall?",)
            for word_counter in range(max_sequence_length):
                encoder_self_attention_mask, decoder_self_attention_mask, decoder_cross_attention_mask= create_masks(eng_sentence, kn_sentence)
                predictions = transformer(eng_sentence,
                                          kn_sentence,
                                          encoder_self_attention_mask.to(device), 
                                          decoder_self_attention_mask.to(device), 
                                          decoder_cross_attention_mask.to(device),
                                          enc_start_token=False,
                                          enc_end_token=False,
                                          dec_start_token=True,
                                          dec_end_token=False)
                next_token_prob_distribution = predictions[0][word_counter] # not actual probs
                next_token_index = torch.argmax(next_token_prob_distribution).item()
                next_token = index_to_kannada[next_token_index]
                kn_sentence = (kn_sentence[0] + next_token, )
                if next_token == END_TOKEN:
                    break
                    
            print(f"Evaluation translation (should we go to the mall?) : {kn_sentence}") #ನಾವು ಮಾಲ್‌ಗೆ ಹೋಗಬೇಕೇ?
            print("-------------------------------------------")
    
    # Calculate precision and F-score
    precision = precision_score(labels.view(-1).cpu(), predictions.view(-1).cpu(), average='weighted', zero_division=1)
    f_score = f1_score(labels.view(-1).cpu(), predictions.view(-1).cpu(), average='weighted')

    start_time = time.time()
    accuracy = total_correct_predictions / total_predictions
    end_time = time.time()
    training_time = end_time - start_time

    print(f"Accuracy after epoch {epoch}: {accuracy}")
    print(f"Precision: {precision}")
    print(f"F-score: {f_score}")
    
    accuracy_list.append(accuracy)
    loss_list.append(loss.item())
    f_score_list.append(f_score)
    precision_list.append(precision)
    


#Final accuracy after training
final_accuracy = total_correct_predictions / total_predictions
print(f"Final Accuracy after training: {final_accuracy}")

Epoch 0
Iteration 0 : 4.167812824249268
English: hes a scientist.
Kannada Translation: ಇವರು ಸಂಶೋಧಕ ಸ್ವಭಾವದವರು.
Kannada Prediction: ು  ್್ ್್  ಿ      ್್ು್್್್್    ಿ ್್್್ ಿ   ನಿ     ಸಸ ಸ   ಿನಾಿ     .      ು್ು ್ ಿ                         ್ ್  ು ು್  ರರತತ ತ       ತ   ್್್ ್ತು ುು್ಾನನ ಿಿುುು್ುತುುುುರಿಿಿಿಿುಿಿಿ್ುು್ು್್ಪು  ್್ು ುುುುನುುು ುಕಕಕಕ ು್್
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ರರರರರರರರರರರ      ಿಿ್್್್್್್ರ್್್್್್್್್್ಿಿಿಿಿಿಿಿಿಿಿಿಿಿಿಿಿಿಿಿಿಿ್್ಿಿಿಿ್್್್್್ುುುರರರರ್ ರರರತತಿಿತರರತತ ು    ್್ರರರರ್ರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರರಿಿಿಿಿಿಿಿುುು್ುಿುುಿಿ್್್ುುುುುರರರರರರಕಕಕಕರರರರ',)
-------------------------------------------
Iteration 100 : 3.529623031616211
English: she ate it.
Kannada Translation: ಅವಳು ಅವನಿಗೆ ಊಟ ಹಾಕಿದಳೂ.
Kannada Prediction: ಕದ್ ು  ಕ ಕ ೆ್  ಕ್ಿ
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ಕದ್                 ್ ್    <END>',)
-------------------------------------------
Iteration 200 : 3.2503905296325684
English: caste and religion 

Evaluation translation (should we go to the mall?) : ('ಅವರ್ಯ ಸಂದು ಸಂದು ಮಾಡಿದ್ದೆ.<END>',)
-------------------------------------------
Iteration 2000 : 2.5219297409057617
English: principal of the college dr
Kannada Translation: ಕಾಲೇಜಿನ ಪ್ರಿನ್ಸಿಪಾಲ ಡಾ.
Kannada Prediction: ಇಾರ್ ್ ್ಮಾರಾಕ್ನಿ ್ರಿಸಿಡ
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ಇದರೆ ಸಂದು ಸಂದು ಮಾಡಿದ್ದಾರೆ.<END>',)
-------------------------------------------
Iteration 2100 : 2.431617498397827
English: apply it on inflamed and rashy areas.
Kannada Translation: ಮೊಡವೆ ಹಾಗೂ ಮೊಡವೆಯ ಕಲೆಗಳು ಇರುವ ಜಾಗಕ್ಕೆ ಇದನ್ನು ಹಚ್ಚಿಕೊಳ್ಳಿ.
Kannada Prediction: ಅಾಂ್ು ಸಾರ್ ಮತಂಿರ  ಅ್್ ೆು ಮಲಿದಾಮಿರಿ್ತೆ ಸದಿಿನು ನಾಿರಿಸೆಳಿತಿದ
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ಅದರೆ ಅವಿಕ್ಟಿ ಮಾರ್ತಿ ಮಾಡಿದೆ.<END>',)
-------------------------------------------
Iteration 2200 : 2.4805233478546143
English: some common terms
Kannada Translation: ಕೆಲವು ಸಾಮಾನ್ಯ ಪದಗಳನ್ನು
Kannada Prediction: ಇಾೕ್  ಕ್ವ್ರುನಾಸ್್ಳು್ನು                    

Iteration 4000 : 2.202258586883545
English: you got questions?
Kannada Translation: ಪ್ರಶ್ನೆಗಳಿವೆಯೆ?
Kannada Prediction: ಅ್ರಾ್ಟೆಯೆುಗು ನ 
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ಆದರೆ ಅವರು ಮಾಡುವುದು ಹೇಳಿಸುವುದು ಮಾಡುತ್ತದೆ?<END>',)
-------------------------------------------
Iteration 4100 : 2.196345329284668
English: directed by zoya akhtar.
Kannada Translation: ಝೋಯಾ ಅಖ್ತರ್ ನಿರ್ದೇಶನದಲ್ಲಿ ಮೂಡಿಬಂದಿದೆ.
Kannada Prediction: ಇಾಗಾನಮವ್ಯು ಥಮಿರುಥೇ ್್್್ಲ. ಮಾಲಿದೇದುದೆ.
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ನಿಮ್ಮ ಮಾಡುವುದು ಮಾಡುವುದು?<END>',)
-------------------------------------------
Iteration 4200 : 2.139482021331787
English: """leaders of both parties of coalition will hold a discussion about the loss of jd(s)-congress coalition candidates."
Kannada Translation: ಹಾಗೆಯೇ ಜೆಡಿಎಸ್-ಕಾಂಗ್ರೆಸ್ ಮೈತ್ರಿ ಅಭ್ಯರ್ಥಿಗಳ ಸೋಲಿನ ಬಗ್ಗೆ ಎರಡು ಪಕ್ಷಗಳ ನಾಯಕರು ಚರ್ಚೆ ನಡೆಸುತ್ತೇವೆ.
Kannada Prediction: ಆಾಗಾ ಾ ಮನರೆಯಂ್  ್ರಡ್ರ  ್ ಮಾತ್ತಿ ಪವಾಯಾ  ಿ ಳ ಕಿದ್ಸ ಮಿ್ಬೆ ಕಂು್ವಮ್್ಷಣೆುಮಿನಿ್ಿ

Iteration 6000 : 2.0870721340179443
English: illayaraja will compose the music for the film, which will have cinematography by ajay vincent.
Kannada Translation: ಇಳಯರಾಜ ಅವರ ಸಂಗೀತ, ಅಜಯ್ ವಿನ್ಸೆಂಟ್ ಅವರ ಛಾಯಾಗ್ರಹಣ ಚಿತ್ರಕ್ಕಿದೆ.
Kannada Prediction: ಇದಿ ಿ ಿಕವರುಸ್ಗ್ರಿ ಮವ್ ಯಮಿವ್ ್ ದ್ ಸವರುಸಾಜಕದಿ  ಾ ಸಿತ್ರಿ್ಕೆದ್ 
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ಅವರು ಅವರು ಮಾಡುತ್ತಿದ್ದೇನೆ?<END>',)
-------------------------------------------
Iteration 6100 : 1.9715139865875244
English: but it didnt keep its promise.
Kannada Translation: ಆದರೆ ಅವರ ಭರವಸೆ ಈಡೇರಲಿಲ್ಲ.
Kannada Prediction: ಆದರೆ ಅವರುಅಾ್ಾ್ ನ ಿರು್ಲ್ಲ.
Bleu Score: 0.08034284189446518
Evaluation translation (should we go to the mall?) : ('ನಾವು ನಿಮ್ಮ ಮಾಡಿದ್ದೇನೆ?<END>',)
-------------------------------------------
Iteration 6200 : 2.020416498184204
English: and it doesnt have any side effects.
Kannada Translation: ಅಲ್ಲದೇ ಯಾವುದೇ ರೀತಿಯ ಅನಾನುಕೂಲಗಳಾಗು ವುದಿಲ್ಲ.
Kannada Prediction: ಇದ್ಲಿೆ ಸಾವು ೇ ಸಾತಿ  ಸವುವು ್ ್ಳುಗಿತಹಿದುದ್ಲ.
Bleu Score: 

Iteration 8100 : 1.7815821170806885
English: it's not a performance.
Kannada Translation: ಇದು ಪ್ರದರ್ಶನ ಕಲೆಯಲ್ಲ.
Kannada Prediction: ಇದರ ಸ್ರಕೇಿಭಿೆಸಾ್ ಲ್ಲಿ
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ಅವರು ಅವರು ಹೇಗೆ ಹೇಗೆ?<END>',)
-------------------------------------------
Iteration 8200 : 1.961072564125061
English: difficulty in breathing,
Kannada Translation: ಉಸಿರಾಟದ ತೊಂದರೆ ಉಪಸ್ಥಿತಿ.
Kannada Prediction: ಮದ್ದುಟ್ಲಮೆರಂಡೆೆ ಮತ್್ತಿತಿ
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ನಿಮ್ಮ ಮಾಡಿದ ಹೇಗೆ ಹೇಗೆ ಹೇಗೆ?<END>',)
-------------------------------------------
Iteration 8300 : 1.906409740447998
English: culture and education
Kannada Translation: ಸಂಸ್ಕೃತಿ ಮತ್ತು ನಾಗರಿಕತೆ
Kannada Prediction: ಮಂಸ್ತರಷಿ ಮತ್ತು ಪಿಯಿಿ
Bleu Score: 0.11362193664674995
Evaluation translation (should we go to the mall?) : ('ಅವರು ಅವರು ಮಾಡುವುದು ಹೇಗೆ ಹೇಗೆ?<END>',)
-------------------------------------------
Iteration 8400 : 1.8937480449676514
English: put all the ingredients in a

...

Evaluation translation (should we go to the mall?) : ('ನಾವು ಸಣ್ಣ ಪಡೆಯಬೇಕೇ?<END>',)
-------------------------------------------
Iteration 14600 : 1.0038079023361206
English: you did not supply a name for that account.
Kannada Translation: ನೀವು ಆ ಖಾತೆಗೆ ಒಂದು ಹೆಸರನ್ನು ಒದಗಿಸಿಲ್ಲ.
Kannada Prediction: ಇಿವು ಖ ರಾತೆ ೆ ಹಂದು ಹೆಸರು್ನು ನಂಗಿಸುಲ್ಲ.
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ನಾವು ಸಣ್ಣ ಪ್ರಾಣಿಗೆ ಹೋಗಬೇಕೇ?<END>',)
-------------------------------------------
Iteration 14700 : 0.9903292655944824
English: anushka sharma and virat kohli - the most talked about couple in indian cricket and bollywood.
Kannada Translation: ಬಾಲಿವುಡ್ ಮತ್ತು ಕ್ರಿಕೆಟ್ ರಂಗದ ಬೆಸುಗೆಯಲ್ಲಿ ತೀರಾ ಇತ್ತೀಚಿನ ಜೋಡಿ ಎಂದರೆ ಅನೂಷ್ಕಾ ಶರ್ಮಾ ಮತ್ತು ಕ್ರಿಕೆಟಿಗ ವಿರಾಟ್ ಕೊಹ್ಲಿ.
Kannada Prediction: ಬಾಲಿವುಡ್ ನತ್ತು ಕ್ರಿಕೆಟ್ ನಾಗ್ಲನಾಂೆವೆ  ್ಲಿ ನಂವ್ ಕಂ್ತೀಚೆನ ಕೋಡಿ ಬಂದುು ನನುಷ್ ಾ ಶರ್ಮಾ ಹತ್ತು ಕ್ರಿಕೆಟ್ಗ ನಿರಾಟ್ ಕೊಹ್ಲಿ 
Bleu Score: 0.01618861356572822
Evaluation translation (should we go to the mall?) : ('ನಾವು ಸಣ್ಣ ಪ್ರಾಣ ಮಾಡಬೇಕೇ?

Evaluation translation (should we go to the mall?) : ('ನಾವು ಅವರಿಗೆ ಹೋಗಬೇಕು?<END>',)
-------------------------------------------
Iteration 16900 : 0.9448438286781311
English: that process is underway.
Kannada Translation: ಈ ಪ್ರಕ್ರಿಯೆ ಜಾರಿಯಲ್ಲಿದೆ.
Kannada Prediction: ಇ ಪ್ರಕ್ರಿಯೆಯಸಾರಿಯಾ್ಲಿದೆ.
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ನಾವು ಅವರಿಗೆ ನಾವು ಸಾಧ್ಯವಾಗಿ ಬೇಕು?<END>',)
-------------------------------------------
Iteration 17000 : 0.9308103322982788
English: against this determination india appealed to the international court of justice.
Kannada Translation: ಇದರ ವಿರುದ್ಧ ಭಾರತ ಅಂತಾರಾಷ್ಟ್ರೀಯ ನ್ಯಾಯಾಲಯದ ಮೆಟ್ಟಿಲೇರಿತ್ತು.
Kannada Prediction: ಈದನ ವಿರುದ್ಧ ಭಾರತ ವಂತರರಾಷ್ಟ್ರೀಯ ನ್ಯಾಯಾಲಯದ ವೇರ್ಟಿಲೇರಿಸ್ತು.
Bleu Score: 0.09554427922043669
Evaluation translation (should we go to the mall?) : ('ನಾವು ಅವರಿಗೆ ನಾವು ಸಾಧ್ಯವಾಗಿ ಹೋಗಬೇಕೇ?<END>',)
-------------------------------------------
Iteration 17100 : 1.0814118385314941
English: we have taken major policy decisions and carried out

Iteration 18800 : 0.9491069316864014
English: is it presumptuous on our part to think that we are the ones who are doing this work?
Kannada Translation: ಯೇಸು ಹೇಳಿದ ಸಾರುವ ಕೆಲಸವನ್ನು ಮಾಡುತ್ತಿರುವವರು ನಾವೇ ಎಂದು ಹೇಳುತ್ತೇವೆ.
Kannada Prediction: ನಾಸು ಕೇಗುದ ಕಂಮ್ವ ಅೆಲಸವನ್ನು ನಾಡುವ್ತಿದುವ ರಿ ಯಮವುನಆಂಬು ನೇಳಿತ್ತಾವೆ?
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ನಾವು ಸಣ್ಣ ಪಡೆಯಬೇಕೇ?<END>',)
-------------------------------------------
Iteration 18900 : 0.9125021696090698
English: a case was registered in police station and investigation was set into motion.
Kannada Translation: ಿವಿ ಪೋಲೀಸ್ ಠಾಣೆಯಲ್ಲಿ ಪ್ರಕರಣ ದಾಖಲಾಗಿದ್ದು ತನಿಖೆ ಮುಂದುವರೆದಿದೆ.
Kannada Prediction: ಈ ಿ ಪೊಲಿಸ್ ಠಾಣೆಯಲ್ಲಿ ಪ್ರಕರಣ ದಾಖಲಾಗಿದ್ದು,ತನಿಖೆ ನುಂದುವರೆಸಿದೆ.
Bleu Score: 0.06985342056580097
Evaluation translation (should we go to the mall?) : ('ನಾವು ಸಣ್ಣ ಸಾಮಾನ್ಯವಾಗಿ ಬೇಕು?<END>',)
-------------------------------------------
Iteration 19000 : 1.0189217329025269
English: add lemon juice to it.
Kannada Translation: ಇದಕ್ಕೆ ನಿಂಬೆರಸ 

Evaluation translation (should we go to the mall?) : ('ನಾವು ಸಣ್ಣ ಪಡೆಯಬೇಕೇ?<END>',)
-------------------------------------------
Iteration 21100 : 0.9154660105705261
English: currently, rs 30 crore are outstanding.
Kannada Translation: ಪ್ರಸಕ್ತ ಸಾಲಿನಲ್ಲಿ 30 ಕೋಟಿ ರೂ.
Kannada Prediction: ಪ್ರಸ್್ತ 3ಂಲಿನ ್ಲಿ 30 ಕೋಟಿ ರೂ.
Bleu Score: 0.20205155046766235
Evaluation translation (should we go to the mall?) : ('ನಾವು ಸಣ್ಣ ಪಡೆಯಬೇಕು?<END>',)
-------------------------------------------
Iteration 21200 : 0.8992297649383545
English: these are the signs you should watch out for:
Kannada Translation: ನೀವು ಮರುಪ್ರಸಾರ ಮಾಡಬೇಕಾದ ಚಿಹ್ನೆಗಳು ಇಲ್ಲಿವೆ:
Kannada Prediction: ಈಿವು ಈಾುವಾರಿ್ದವಕಾಡುೇಕುದ ಅಿಹ್ನೆಗಳು ಇವ್ಲಿವೆ:
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ನಾವು ಸಣ್ಣ ಸಾಧ್ಯವಾಗಿ ಹೋಗಬೇಕು?<END>',)
-------------------------------------------
Iteration 21300 : 0.9575278162956238
English: (top-right picture)
Kannada Translation: (ಚಿತ್ರದಲ್ಲಿ ಅತೀ ಎಡಗಡೆ)
Kannada Prediction: (ಚಿತ್ರ  ್ಲಿ ಚಡ್ ಚತೆೈೆ 
Bleu 

Evaluation translation (should we go to the mall?) : ('ನಾವು ಮಾಡಬೇಕೆಂದು ನಾವು ಹೋಗಬೇಕೇ?<END>',)
-------------------------------------------
Iteration 23400 : 0.9675893783569336
English: equality for all
Kannada Translation: ಸರ್ವರಿಗೂ ಸಮಾನತೆಯ ಹಕ್ಕು
Kannada Prediction: ಎಮಿವ ಿಗೂ ಗಮಾನವಾ ನಗಾ್ಕು
Bleu Score: 0
Evaluation translation (should we go to the mall?) : ('ನಾವು ಮಾಡಬೇಕೆಂದು ನಾವು ಹೋಗಬೇಕೇ?<END>',)
-------------------------------------------
Iteration 23500 : 0.9262358546257019
English: the new york police department also recorded a similar spike.
Kannada Translation: ನ್ಯೂಯಾರ್ಕ್ ಪೊಲೀಸ್ ಇಲಾಖೆ ಸಹ ಇಂತಹ ಅಪರಾಧಗಳು ಹೆಚ್ಚಾಗಿರುವುದನ್ನು ದಾಖಲಿಸಿದೆ.
Kannada Prediction: ಈ್ಯೂಯಾರ್ಕ್ ಇೊಲೀಸರ ಇಲಾಖೆ ಇಂ ಇದಥಹ ಇವಘಾಧ ಳನ ಸೊಚ್ಚಿಗಿದುವ ದಾ್ನು ದಾಖಲಿಸಿದ್.
Bleu Score: 0.021105340631872645
Evaluation translation (should we go to the mall?) : ('ನಾವು ಮಾಡಬೇಕೆಂದು ನಾವು ಹೋಗಬೇಕೇ?<END>',)
-------------------------------------------
Iteration 23600 : 1.0078009366989136
English: he is the real hero.
Kannada Translation: ನಿಜವಾದ ಹೀರೋ ಅವರ

In [ ]:
plt.figure(figsize=(10, 5))

plt.subplot(1, 2, 1)
plt.plot(range(num_epochs), accuracy_list, label='Accuracy', color='b', marker='o')
plt.title('Accuracy During Training')
plt.xlabel('Epochs')
plt.ylabel('Accuracy')
plt.legend()

# Plotting the loss
plt.subplot(1, 2, 2)
plt.plot(range(num_epochs), loss_list, label='Loss', color='r', marker='o')
plt.title('Loss During Training')
plt.xlabel('Epochs')
plt.ylabel('Loss')
plt.legend()

plt.tight_layout()
plt.show()

In [ ]:
# Plotting F-score
plt.figure(figsize=(10, 5))
plt.plot(range(num_epochs), f_score_list, label='F-score', marker='o')
plt.title('F-score Over Epochs')
plt.xlabel('Epochs')
plt.ylabel('F-score')
plt.legend()
plt.show()

# Plotting Precision
plt.figure(figsize=(10, 5))
plt.plot(range(num_epochs), precision_list, label='Precision', marker='o')
plt.title('Precision Over Epochs')
plt.xlabel('Epochs')
plt.ylabel('Precision')
plt.legend()
plt.show()

In [ ]:
len(kannada_translation_list), len(kannada_prediction_list)

In [ ]:
kannada_translation_list

In [ ]:
kannada_prediction_list

In [ ]:

# # Use smoothing function
# smooth = SmoothingFunction()

# # Calculate BLEU scores for each pair
# for generated, reference in zip(kannada_prediction_list, kannada_translation_list):
#     generated_tokens = generated.split()
#     reference_tokens = reference.split()
#     bleu_score = sentence_bleu([reference_tokens], generated_tokens, smoothing_function=smooth.method1)
    
#     if bleu_score >= 0.2:
        
#         print(generated)
#         print(reference)
#         print(f"BLEU Score for Pair: {bleu_score}")
#         print("=======================================")

In [ ]:
from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction

def calculate_bleu_score(reference, candidate, smoothing_function):
    reference_tokens = reference.split()
    candidate_tokens = candidate.split()

    # Calculate BLEU score for a single pair
    return sentence_bleu([reference_tokens], candidate_tokens, smoothing_function=smoothing_function)

def save_results_to_file(output_file, pairs):
    with open(output_file, 'w', encoding='utf-8') as file:
        file.write("Generated Sentence\tReference Sentence\tBLEU Score\n")
        for generated, reference, bleu_score in pairs:
            file.write(f"{generated}\t{reference}\t{bleu_score}\n")

if __name__ == "__main__":
    from nltk.translate.bleu_score import SmoothingFunction

    smooth = SmoothingFunction()

    output_file = "bleu_scores_results-1.txt"
    result_pairs = []

    for generated, reference english in zip(kannada_prediction_list, kannada_translation_list, english_list):
        bleu_score = calculate_bleu_score(reference, generated, smoothing_function=smooth.method1)

        if bleu_score >= 0.2:
            print(f"English Sentence: {english}")
            print(f"Generated Sentence: {generated}")
            print(f"Reference Sentence: {reference}")
            print(f"BLEU Score for Pair: {bleu_score}")
            print("=======================================")

            # Append the result to the list
            result_pairs.append((generated, reference, bleu_score))

    # Save results to file
    save_results_to_file(output_file, result_pairs)

    print(f"Results saved to {output_file}")